In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC

import pandas as pd

In [ ]:
driver = webdriver.Chrome()
driver.get("https://webgate.ec.europa.eu/fleet-europa/search_en")

wait = WebDriverWait(driver, 1)

# Hacer clic en el botón "EU"
eu_option = wait.until(EC.element_to_be_clickable((By.XPATH, "//label[@for='countryType1']")))
eu_option.click()

# Hacer click en "All Vessels"
all_vessels_option = wait.until(EC.element_to_be_clickable((By.XPATH, "//label[@for='period1']")))
all_vessels_option.click()

# Hacer clic en el botón "Search"
btn_search = wait.until(EC.element_to_be_clickable((By.XPATH, "//button/span[text()='Search']")))
btn_search.click()


#-----------------------------------------------------------------------------------------------------#

# Esperar a que el selector de la página de resultados se muestre
wait.until(EC.presence_of_element_located((By.CLASS_NAME, "select2-selection--single")))

page_size_selector = driver.find_element(By.CLASS_NAME, "select2-selection--single")
page_size_selector.click()

# Esperar a que la lista con opciones sea visible
wait.until(EC.presence_of_element_located((By.XPATH, "//ul[@class='select2-results__options']")))

# Intentar hacer clic en la opción que contiene el texto "100"
page_size_100 = wait.until(EC.element_to_be_clickable((By.XPATH, "//li[contains(text(),'100')]")))

# Hacer clic en la opción "100"
page_size_100.click()
#-----------------------------------------------------------------------------------------------------#
# Esperar a que la tabla cargue
wait.until(EC.presence_of_element_located((By.CLASS_NAME, "table-header-container")))

# Nº de resultados por página 100
page_size_selector = driver.find_element(By.CLASS_NAME, "select2-selection--single")
page_size_selector.click()

# Extraer los nombres de las columnas 
column_headers = driver.find_elements(By.XPATH, "//div[@class='table-header-container']/span")
column_names = [header.text.strip() for header in column_headers] 

# Contenido de las filas
rows = driver.find_elements(By.XPATH, "//table/tbody/tr")

data = []

while True:
    # Extraer filas de la tabla
    rows = driver.find_elements(By.XPATH, "//table/tbody/tr")
    
    for row in rows:
        cells = row.find_elements(By.TAG_NAME, "td")
        row_data = [cell.text.strip() for cell in cells]  
        data.append(row_data)

    # Intentar encontrar el botón "Next"
    try:
        # Buscar el botón "Next" usando el atributo aria-label
        next_button = wait.until(EC.element_to_be_clickable((By.XPATH, "//a[@aria-label='Go to next page']")))

        # Desplazar hasta el botón "Next"
        driver.execute_script("arguments[0].scrollIntoView(true);", next_button)
        
        # Verificar si el botón "Next" está habilitado
        if "disabled" not in next_button.get_attribute("class"):  
            # Hacer clic en el botón "Next"
            next_button.click()
            wait.until(EC.presence_of_element_located((By.TAG_NAME, "table")))  # Esperar a que la nueva página cargue
        else:
            break  # Si el botón está deshabilitado, salir del bucle
    except:
        break  # Si no hay botón "Next" o hubo un error, salir del bucle
   

# Crear DataFrame con todos los datos recopilados
df = pd.DataFrame(data, columns=column_names)

# Cerrar el driver
driver.quit()

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 185354 entries, 0 to 185353
Data columns (total 14 columns):
 #   Column               Non-Null Count   Dtype 
---  ------               --------------   ----- 
 0   Flag                 185354 non-null  object
 1   Vessel Type          185354 non-null  object
 2   CFR                  185354 non-null  object
 3   Event Code           185354 non-null  object
 4   Event Date           185354 non-null  object
 5   External Marking     185354 non-null  object
 6   Vessel Name          185354 non-null  object
 7   Ref. Tonnage         185354 non-null  object
 8   Ref. Length          185354 non-null  object
 9   Main Power           185354 non-null  object
 10  IRCS                 185354 non-null  object
 11  UVI                  185354 non-null  object
 12  Highest Error Level  185354 non-null  object
 13  Reception Timestamp  185354 non-null  object
dtypes: object(14)
memory usage: 19.8+ MB


In [5]:
df.head()

Flag Vessel Type           CFR Event Code  Event Date External Marking  \
0  BEL          FX  BEL000021964        DES  27/02/2023              O.2   
1  BEL          TU  BEL000041982        RET  15/11/1996            BOU 4   
2  NLD          TU  BEL000041982        MOD  07/06/2024             BR-9   
3  BEL          FX  BEL000061930        DES  30/08/1996            BOU 6   
4  BEL          TU  BEL000071985        EXP  24/04/2018            BOU.7   

      Vessel Name Ref. Tonnage Ref. Length Main Power    IRCS      UVI  \
0  MIKE MICHEL JR         53.0       21.39      213.0    OPAB  8523448   
1          ASTRID        15.67       13.85       79.0    OPAD            
2          BOURIC         14.0       14.36       83.0  PA2442            
3            ANJA        29.79       16.62      103.0    OPAF            
4   DE ENIGE ZOON         57.0        19.1      219.0    OPAG            

  Highest Error Level  Reception Timestamp  
0                 ERR  01/03/2023 14:47:06  
1                      09/09/2019 12:50:19  
2                      07/06/2024 23:18:25  
3                      09/09/2019 12:50:19  
4                 MAJ  09/09/2019 12:50:19

In [6]:
df.to_csv("./data/resultados_fleet.csv", index=False, encoding='utf-8')

In [7]:
driver

<selenium.webdriver.chrome.webdriver.WebDriver (session="2069b2060e15c48ebcb41db9af2d08d8")>

Por otro lado, este utiliza BeautifulSoup para automatizar la extracción de datos desde el sitio web del Registro General de la Flota Pesquera Española. El script automatiza la búsqueda de todos los barcos registrados consultando a través del campo 'CFR' que se encuentra en el dataset 'resultados_fleet.csv', navega a través de las páginas de resultados y guarda los datos en un archivo CSV. Para esto ejecuta las siguientes celdas del cuaderno.

In [2]:
import pandas as pd
import requests
from bs4 import BeautifulSoup

In [3]:
# Cargar el dataset
file_path = r"/Users/macbookairjulio/Documents/GitHub/repo_tipologia/data/resultados_fleet.csv"
df = pd.read_csv(file_path, dtype=str)  # Leer como string para evitar problemas de formato

# Mostrar las primeras filas para entender la estructura
df.head()

Flag Vessel Type           CFR Event Code  Event Date External Marking  \
0  BEL          FX  BEL000021964        DES  27/02/2023              O.2   
1  BEL          TU  BEL000041982        RET  15/11/1996            BOU 4   
2  NLD          TU  BEL000041982        MOD  07/06/2024             BR-9   
3  BEL          FX  BEL000061930        DES  30/08/1996            BOU 6   
4  BEL          TU  BEL000071985        EXP  24/04/2018            BOU.7   

      Vessel Name Ref. Tonnage Ref. Length Main Power    IRCS      UVI  \
0  MIKE MICHEL JR         53.0       21.39      213.0    OPAB  8523448   
1          ASTRID        15.67       13.85       79.0    OPAD      NaN   
2          BOURIC         14.0       14.36       83.0  PA2442      NaN   
3            ANJA        29.79       16.62      103.0    OPAF      NaN   
4   DE ENIGE ZOON         57.0        19.1      219.0    OPAG      NaN   

  Highest Error Level  Reception Timestamp  
0                 ERR  01/03/2023 14:47:06  
1                 NaN  09/09/2019 12:50:19  
2                 NaN  07/06/2024 23:18:25  
3                 NaN  09/09/2019 12:50:19  
4                 MAJ  09/09/2019 12:50:19

In [4]:
# Filtrar solo los buques de España
df_esp = df[df["Flag"] == "ESP"].copy()

# Obtener la cantidad de buques españoles
num_buques_esp = df_esp.shape[0]

# Mostrar las primeras filas después del filtrado
df_esp.describe()

Flag Vessel Type           CFR Event Code  Event Date  \
count   27484       27484         27484      27484       27484   
unique      1           5         27484          7        5556   
top       ESP          FX  ESP000000001        DES  13/03/2001   
freq    27484       27478             1      12469         950   

       External Marking Vessel Name Ref. Tonnage Ref. Length Main Power  IRCS  \
count             27484       27484        27484       27484      27484  6875   
unique            27476       19706         6055        2750       1933  6286   
top       3-7PM-1369-91       MARIA          1.5         5.0        0.0  EADI   
freq                  2         150          184         492       2726     4   

            UVI Highest Error Level  Reception Timestamp  
count      1116                1563                27484  
unique     1116                   3                 5535  
top     8799762                 MAJ  06/06/2018 02:00:00  
freq          1                 903                13104

In [22]:
# Obtener la lista de identificadores únicos CFR
cfr_list = df_esp["CFR"].dropna().unique().tolist()

# Mostrar los primeros 10 CFR para verificar
cfr_list[:10]

['ESP000000001',
 'ESP000000002',
 'ESP000000003',
 'ESP000000004',
 'ESP000000005',
 'ESP000000006',
 'ESP000000007',
 'ESP000000008',
 'ESP000000009',
 'ESP000000010']

In [9]:
import requests
from bs4 import BeautifulSoup

# URL del sitio web
url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Crear una sesión para mantener cookies y encabezados
session = requests.Session()

# Hacer la solicitud GET a la página
response = session.get(url)

# Verificar que la solicitud fue exitosa
if response.status_code == 200:
    soup = BeautifulSoup(response.text, "html.parser")
    print(soup.prettify())  # Muestra el HTML de la página
else:
    print("Error al acceder a la página:", response.status_code)


<!DOCTYPE html>
<html lang="es">
 <head>
  <meta charset="utf-8"/>
  <meta content="width=device-width, initial-scale=1.0" name="viewport"/>
  <link href="/CENSO/ConsultaBuqueRegistro/favicon.ico" rel="shortcut icon" type="image/x-icon"/>
  <title>
   Búsqueda de buques - Registro General de la Flota Pesquera
  </title>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/bootstrap/bootstrapf12g24?v=TGfFO1If-ULZb946e3Q565IQRQVoMwtE6A2bSIDxhbM1" rel="stylesheet"/>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/fenixcss?v=z42NHXCPbhKYjIilJT7muAWV6_9v6erQJ2VakY9JTvE1" rel="stylesheet"/>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/css?v=h0rTCPdZqqV6ErwAKJoYgjWvKYV9ApclMeslYMhnwyg1" rel="stylesheet"/>
 </head>
 <body>
  <header class="fenixHeader">
   <img alt="Ministerio de Agricultura, Pesca y Alimentación" class="titulo-logo" src="/CENSO/ConsultaBuqueRegistro/Content/images/iconos/LogoFenixh70.png"/>
   <h1 class="titulo-aplicacion">
    Registro General de la Flota Pesquera
   

El formulario de búsqueda utiliza una solicitud GET con el parámetro text para buscar el CFR en la siguiente URL:

```ruby
https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search?text=ESP000000001
```

In [10]:
# URL base de búsqueda
base_url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Parámetro de búsqueda (CFR)
params = {"text": "ESP000000001"}

# Realizar la solicitud GET con el CFR
response = requests.get(base_url, params=params)

# Verificar si la solicitud fue exitosa
if response.status_code == 200:
    soup = BeautifulSoup(response.text, "html.parser")
    
    # Mostrar el HTML de la respuesta (para analizar la estructura)
    print(soup.prettify())
    
    # Aquí puedes extraer los datos específicos según la estructura HTML
else:
    print(f"Error {response.status_code}: No se pudo acceder a la página")


<!DOCTYPE html>
<html lang="es">
 <head>
  <meta charset="utf-8"/>
  <meta content="width=device-width, initial-scale=1.0" name="viewport"/>
  <link href="/CENSO/ConsultaBuqueRegistro/favicon.ico" rel="shortcut icon" type="image/x-icon"/>
  <title>
   Resultado de la búsqueda de "ESP000000001", página 1 - Registro General de la Flota Pesquera
  </title>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/bootstrap/bootstrapf12g24?v=TGfFO1If-ULZb946e3Q565IQRQVoMwtE6A2bSIDxhbM1" rel="stylesheet"/>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/fenixcss?v=z42NHXCPbhKYjIilJT7muAWV6_9v6erQJ2VakY9JTvE1" rel="stylesheet"/>
  <link href="/CENSO/ConsultaBuqueRegistro/Content/css?v=h0rTCPdZqqV6ErwAKJoYgjWvKYV9ApclMeslYMhnwyg1" rel="stylesheet"/>
 </head>
 <body>
  <header class="fenixHeader">
   <img alt="Ministerio de Agricultura, Pesca y Alimentación" class="titulo-logo" src="/CENSO/ConsultaBuqueRegistro/Content/images/iconos/LogoFenixh70.png"/>
   <h1 class="titulo-aplicacion">
    Registr

Ahora podemos hacer lo siguiente:
- Extraer la URL del buque de los resultados de búsqueda.
- Realizar una solicitud a esa URL para obtener la información técnica del buque.
- Extraer la información clave de la página de detalles.

In [ ]:
# URL base de búsqueda
base_url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Parámetro de búsqueda (CFR)
params = {"text": "ESP000000001"}

# Crear sesión para mantener cookies
session = requests.Session()

# Realizar la solicitud GET con el CFR
response = session.get(base_url, params=params)

# Verificar si la solicitud fue exitosa
if response.status_code == 200:
    soup = BeautifulSoup(response.text, "html.parser")
    
    # Buscar el enlace del buque
    buque_link = soup.find("a", class_="apply--emphasize")
    
    if buque_link:
        # Construir la URL completa del buque
        buque_url = "https://servicio.pesca.mapama.es" + buque_link["href"]
        print(f"Accediendo a: {buque_url}")
        
        # Realizar la solicitud a la página del buque
        buque_response = session.get(buque_url)
        
        if buque_response.status_code == 200:
            buque_soup = BeautifulSoup(buque_response.text, "html.parser")
            
            # Extraer el nombre del buque
            nombre_buque = buque_soup.find("h2", class_="title--vessel-details").text.split("Nombre: ")[-1]
            
            # Extraer todos los datos clave
            datos_buque = {}
            for div in buque_soup.find_all("div"):
                label = div.find("dt", class_="info-field--label")
                value = div.find("dd", class_="info-field--value")
                if label and value:
                    datos_buque[label.text.strip()] = value.text.strip()

            # Mostrar resultados
            print(f"Nombre del buque: {nombre_buque}")
            for key, value in datos_buque.items():
                print(f"{key}: {value}")
        else:
            print(f"Error {buque_response.status_code}: No se pudo acceder a la página del buque")
    else:
        print("No se encontró el enlace del buque")
else:
    print(f"Error {response.status_code}: No se pudo acceder a la página de búsqueda")


Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26006?foundSearchingText=ESP000000001&foundInPage=1
Nombre del buque: ARGOÑOS
CFR: ESP000000001
IMO: -
IRCS: EA7682
Matrícula: 3ST-4-2467
Alta en RGFP: 10/05/1989
Estado: Baja Definitiva (desde el 02/12/1998)
Eslora total: 0,00 m
Arqueo GT: 52,70
Potencia: 202,26 kW (275,0 CV)
Material del casco: Madera
Puerto base: 21250 - Vicedo, LUGO (GALICIA)
Administración responsable del Registro: Secretaría General de Pesca
Censo por modalidad: CERCO EN CANTABRICO NW


In [ ]:
# URL base de búsqueda
base_url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Parámetro de búsqueda (CFR)
params = {"text": "ESP000000001"}

# Crear sesión para mantener cookies
session = requests.Session()

# Realizar la solicitud GET con el CFR
response = session.get(base_url, params=params)

# Verificar si la solicitud fue exitosa
if response.status_code == 200:
    soup = BeautifulSoup(response.text, "html.parser")
    
    # Buscar el enlace del buque
    buque_link = soup.find("a", class_="apply--emphasize")
    
    if buque_link:
        # Construir la URL completa del buque
        buque_url = "https://servicio.pesca.mapama.es" + buque_link["href"]
        print(f"Accediendo a: {buque_url}")
        
        # Realizar la solicitud a la página del buque
        buque_response = session.get(buque_url)
        
        if buque_response.status_code == 200:
            buque_soup = BeautifulSoup(buque_response.text, "html.parser")
            
            # Extraer el nombre del buque
            nombre_buque = buque_soup.find("h2", class_="title--vessel-details").text.split("Nombre: ")[-1]
            
            # Extraer todos los datos clave
            datos_buque = {"Nombre": nombre_buque}
            for div in buque_soup.find_all("div"):
                label = div.find("dt", class_="info-field--label")
                value = div.find("dd", class_="info-field--value")
                if label and value:
                    datos_buque[label.text.strip()] = value.text.strip()
            
            # Crear DataFrame
            df = pd.DataFrame([datos_buque])
            print(df)
            
        else:
            print(f"Error {buque_response.status_code}: No se pudo acceder a la página del buque")
    else:
        print("No se encontró el enlace del buque")
else:
    print(f"Error {response.status_code}: No se pudo acceder a la página de búsqueda")


Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26006?foundSearchingText=ESP000000001&foundInPage=1
    Nombre           CFR IMO    IRCS   Matrícula Alta en RGFP  \
0  ARGOÑOS  ESP000000001   -  EA7682  3ST-4-2467   10/05/1989   

                                  Estado Eslora total Arqueo GT  \
0  Baja Definitiva (desde el 02/12/1998)       0,00 m     52,70   

               Potencia Material del casco                     Puerto base  \
0  202,26 kW (275,0 CV)             Madera  21250 - Vicedo, LUGO (GALICIA)   

  Administración responsable del Registro     Censo por modalidad  
0             Secretaría General de Pesca  CERCO EN CANTABRICO NW  


In [17]:
df

Nombre           CFR IMO    IRCS   Matrícula Alta en RGFP  \
0  ARGOÑOS  ESP000000001   -  EA7682  3ST-4-2467   10/05/1989   

                                  Estado Eslora total Arqueo GT  \
0  Baja Definitiva (desde el 02/12/1998)       0,00 m     52,70   

               Potencia Material del casco                     Puerto base  \
0  202,26 kW (275,0 CV)             Madera  21250 - Vicedo, LUGO (GALICIA)   

  Administración responsable del Registro     Censo por modalidad  
0             Secretaría General de Pesca  CERCO EN CANTABRICO NW

In [23]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

# URL base de búsqueda
base_url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Crear sesión para mantener cookies
session = requests.Session()

# Lista para almacenar los datos de los buques
data = []

for index, cfr in enumerate(cfr_list, start=1):
    print(f"Procesando {index}/{len(cfr_list)}: CFR {cfr}")
    params = {"text": cfr}
    response = session.get(base_url, params=params)
    
    if response.status_code == 200:
        soup = BeautifulSoup(response.text, "html.parser")
        buque_link = soup.find("a", class_="apply--emphasize")
        
        if buque_link:
            buque_url = "https://servicio.pesca.mapama.es" + buque_link["href"]
            print(f"Accediendo a: {buque_url}")
            buque_response = session.get(buque_url)
            
            if buque_response.status_code == 200:
                buque_soup = BeautifulSoup(buque_response.text, "html.parser")
                nombre_buque = buque_soup.find("h2", class_="title--vessel-details").text.split("Nombre: ")[-1]
                print(f"Buque encontrado: {nombre_buque}")
                
                datos_buque = {"CFR": cfr, "Nombre": nombre_buque}
                
                for div in buque_soup.find_all("div"):
                    label = div.find("dt", class_="info-field--label")
                    value = div.find("dd", class_="info-field--value")
                    if label and value:
                        datos_buque[label.text.strip()] = value.text.strip()
                
                data.append(datos_buque)
            else:
                print(f"Error {buque_response.status_code}: No se pudo acceder a la página del buque {cfr}")
        else:
            print(f"No se encontró el enlace del buque para CFR {cfr}")
    else:
        print(f"Error {response.status_code}: No se pudo acceder a la página de búsqueda para CFR {cfr}")

# Crear DataFrame con los datos obtenidos
df = pd.DataFrame(data)
print("Extracción completada. Resultado final:")
print(df)

Procesando 1/27484: CFR ESP000000001
Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26006?foundSearchingText=ESP000000001&foundInPage=1
Buque encontrado: ARGOÑOS
Procesando 2/27484: CFR ESP000000002
Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26007?foundSearchingText=ESP000000002&foundInPage=1
Buque encontrado: MARIA INSOLINA
Procesando 3/27484: CFR ESP000000003
Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26008?foundSearchingText=ESP000000003&foundInPage=1
Buque encontrado: MOWINKEL II
Procesando 4/27484: CFR ESP000000004
Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26009?foundSearchingText=ESP000000004&foundInPage=1
Buque encontrado: JULIA NUMERO TRES
Procesando 5/27484: CFR ESP000000005
Accediendo a: https://servicio.pesca.mapama.es/CENSO/ConsultaBuqueRegistro/Buques/Details/26010?foundSearchingText=ESP0000

In [25]:
# Guardar los datos en un archivo CSV
output_file = r"/Users/macbookairjulio/Documents/GitHub/repo_tipologia/data/datos_buques_ESP.csv"
df.to_csv(output_file, encoding="utf-8", index=False)
print(f"\nDatos guardados en {output_file}")


Datos guardados en /Users/macbookairjulio/Documents/GitHub/repo_tipologia/data/datos_buques_ESP.csv


1️⃣ Configuración Inicial

- Se define la URL base donde se buscarán los buques en función del CFR.
- Se crea una sesión de requests (session) para mantener cookies y evitar que se reinicie la conexión en cada solicitud.
- Se inicializan dos listas:
    - data: Para almacenar la información extraída de cada buque.
    - cfrs_sin_buque: Para guardar los CFRs que no tienen un buque asociado.

2️⃣ Bucle para recorrer la lista de CFRs

- Se obtiene el número total de CFRs (total_cfrs) para mostrar el progreso.
- Se usa enumerate(cfr_list, start=1) para recorrer cfr_list con un índice que empieza en 1.
- Imprime el progreso, mostrando cuál CFR se está procesando y cuántos faltan.

3️⃣ Realizar la búsqueda del CFR

- Se envía una solicitud GET a la URL de búsqueda con el CFR como parámetro.
- Se verifica si la respuesta tiene el código 200 (éxito) antes de continuar.

4️⃣ Extraer el enlace del buque

- Se analiza el HTML con BeautifulSoup.
- Se busca un enlace con la clase apply--emphasize, que es el que lleva a la página de detalles del buque.

5️⃣ Verificar si existe un buque asociado

- Si buque_link existe, significa que hay un buque asociado al CFR.
- Si no existe, se agrega el CFR a cfrs_sin_buque y se pasa al siguiente.

6️⃣ Acceder a la página del buque

- Se construye la URL completa del buque y se hace otra solicitud GET.
- Se verifica que la respuesta sea 200 (éxito) antes de extraer los datos.

7️⃣ Extraer la información del buque

- Se analiza el HTML de la página del buque con BeautifulSoup.
- Se busca el nombre del buque dentro del "< h2 class="title--vessel-details">."

8️⃣ Extraer los detalles del buque

- Se crea un diccionario datos_buque con CFR y nombre.
- Se recorre la página buscando etiquetas < dt> (etiqueta) y < dd> (valor).
- Se guarda la información en datos_buque y se añade a la lista data.

9️⃣ Manejo de errores

- Si la solicitud a la página del buque falla, se muestra un error y el CFR se agrega a cfrs_sin_buque.

🔟 Si no se encontró un buque

- Si no se encontró un enlace de buque en la página de búsqueda, se guarda el CFR en cfrs_sin_buque.

1️⃣1️⃣ Si la búsqueda del CFR falla

- Si la búsqueda del CFR falla (ej. error 500 o 404), se agrega a cfrs_sin_buque.

1️⃣2️⃣ Crear DataFrame y mostrar resultados

- Se crea un DataFrame de pandas con los datos obtenidos.
- Se imprime el DataFrame.

1️⃣3️⃣ Mostrar los CFRs sin buque

- Si hay CFRs en cfrs_sin_buque, se muestran en pantalla.

In [ ]:
# URL base de búsqueda
base_url = "https://servicio.pesca.mapama.es/censo/ConsultaBuqueRegistro/Buques/Search"

# Crear sesión para mantener cookies
session = requests.Session()

# Lista para almacenar los datos de los buques
data = []
# Lista para almacenar los CFRs sin buque asociado
cfrs_sin_buque = []

# Iterar sobre la lista de CFRs
total_cfrs = len(cfr_list)

# Mostrar el progreso
for index, cfr in enumerate(cfr_list, start=1):
    print(f"Procesando {index}/{total_cfrs}: CFR {cfr}")
    # Realizar la búsqueda del CFR
    params = {"text": cfr}
    # Realizar la solicitud GET con el CFR
    response = session.get(base_url, params=params)
    
    # Verificar si la solicitud fue exitosa
    if response.status_code == 200:
        # Analizar la respuesta HTML con BeautifulSoup
        soup = BeautifulSoup(response.text, "html.parser")
        # Buscar el pagina de detalles del buque
        buque_link = soup.find("a", class_="apply--emphasize")
        
        # Si se encuentra el enlace del buque, acceder a la página de detalles
        if buque_link:
            # Construir la URL completa del buque
            buque_url = "https://servicio.pesca.mapama.es" + buque_link["href"]
            # Realizar la solicitud a la página del buque
            buque_response = session.get(buque_url)
            
            # Verificar si la solicitud fue exitosa antes de extraer los datos
            if buque_response.status_code == 200:
                # Analizar la respuesta HTML de la página del buque
                buque_soup = BeautifulSoup(buque_response.text, "html.parser")
                # Extraer el nombre del buque
                nombre_buque = buque_soup.find("h2", class_="title--vessel-details").text.split("Nombre: ")[-1]
                
                # Crear un diccionario con CFR y nombre del buque
                datos_buque = {"CFR": cfr, "Nombre": nombre_buque}
                
                # Recorrer la pagina buscando etiquetas <div> para extraer los datos
                for div in buque_soup.find_all("div"):
                    label = div.find("dt", class_="info-field--label")
                    value = div.find("dd", class_="info-field--value")
                    if label and value:
                        datos_buque[label.text.strip()] = value.text.strip()
                
                # Agregar los datos del buque a la lista
                data.append(datos_buque)
                print(f"✔️ Datos extraídos para {cfr} ({nombre_buque})")
            # Si no se pudo acceder a la página del buque, registrar el CFR    
            else:
                print(f"❌ Error {buque_response.status_code}: No se pudo acceder a la página del buque {cfr}")
                cfrs_sin_buque.append(cfr)
        # Si no se encontró el enlace del buque, registrar el CFR
        else:
            print(f"⚠️ No se encontró un buque asociado para CFR {cfr}")
            cfrs_sin_buque.append(cfr)
    # Si no se pudo acceder a la página de búsqueda, registrar el CFR
    else:
        print(f"❌ Error {response.status_code}: No se pudo acceder a la página de búsqueda para CFR {cfr}")
        cfrs_sin_buque.append(cfr)

# Crear DataFrame con los datos obtenidos
df = pd.DataFrame(data)
print("\nExtracción finalizada.")
print(df)

# Mostrar CFRs sin buque asociado
if cfrs_sin_buque:
    print("\nCFRs sin buque asociado:")
    print(cfrs_sin_buque)
